# Train Fluid Flow slow manifold Machine


Consider the nonlinear mean-field model of fluid flow past a circular cylinder at Reynolds number 100, described by empirical Galerkin model:
$$
\frac{\partial x_{1}}{\partial t} = \mu x_{1} - \omega x_{2} + A x_{1}x_{3}
$$
$$
\frac{\partial x_{2}}{\partial t} = \omega x_{1} + \mu x_{2} + Ax_{2}x_{3}
$$
$$
\frac{\partial x_{3}}{\partial t} = -\lambda(x_{3} - {x_{1}}^{2} - {x_{2}}^{2}) 
$$

Where $\mu = 0.1, \omega = 1, A=-0.1, \lambda = 10$

In [2]:
%load_ext autoreload
%autoreload 2

In [3]:
import os

os.environ['TF_CPP_MIN_LOG_LEVEL'] = '3'
import tensorflow as tf
from dmd_machine.dmd_ae_machine import DMDMachine
from dmd_machine.loss_function import LossFunction
from data.Data import DataMaker
from datetime import date 
from tensorflow.keras.models import model_from_json
from return_stats import *
from create_plots import *
from datetime import date  
import pickle
import time

plt.rcParams['figure.figsize'] = [15, 8]
plt.rcParams['figure.facecolor'] = 'white'
%matplotlib inline

In [4]:
# ======================================================================================================================
# Read in dataset.
# ======================================================================================================================

training_data = pickle.load(open('./data/dataset_fluid.pkl', 'rb'))

data = training_data.data_val

In [5]:
# Network Hyper Parameters.
hyp_params = dict()
hyp_params['num_t_steps'] = training_data.params['num_time_steps']
hyp_params['phys_dim'] = training_data.params["num_physical_dim"]
hyp_params['num_init_conds'] = training_data.params['num_initial_conditions']
hyp_params['batch_size'] = 256
hyp_params['num_epochs'] = 200

# Encoding/Decoding Layer Parameters.
hyp_params['num_en_layers'] = 3
hyp_params['num_en_neurons'] = 80
hyp_params['latent_dim'] = 3
hyp_params['window_size'] = 256

hyp_params['activation'] = 'elu'
hyp_params['weight_initializer'] = 'he_uniform'
hyp_params['bias_initializer'] = 'he_uniform'
hyp_params['ae_output_activation'] = "linear"
hyp_params['hidden_activation'] = "elu"

hyp_params['c1'] = 1  # coefficient auto-encoder loss.
hyp_params['c2'] = 1  # coefficient of dmd loss.
hyp_params['c3'] = 1  # coefficient of pred loss.

save_folder = "AeEx3_" + str(date.today().isoformat()) # save results in the folder " Results/save_folder"-
# including loss curves and plot latent data.

In [22]:
# ======================================================================================================================
# Prepare dataset. 
# ======================================================================================================================
# convert input data from numpy to tensorflow.
input_data = training_data.data_val
#all_data = tf.data.Dataset.from_tensor_slices(input_data)

# shuffle the dataset and then divide to training vs testing data sets. 80% training .20% testing.
all_data_shuffle = all_data.shuffle(hyp_params['num_init_conds'], seed=42)
data_train = all_data_shuffle.take(int(0.8 * hyp_params['num_init_conds']))
data_test = all_data_shuffle.skip(int(0.8 * hyp_params['num_init_conds']))
#data_train = tf.data.Dataset.from_tensor_slices(all_data_shuffle[:0.8 * hyp_params['num_init_conds'], :, :])
#data_test = tf.data.Dataset.from_tensor_slices(all_data_shuffle[0.8 * hyp_params['num_init_conds']:, :, :])


In [20]:
for data in data_train:
    print(data[0, :])

tf.Tensor(
[ 0.387598    0.4141039   0.43972123  0.46437865  0.48800713  0.51054
  0.5319133   0.55206555  0.5709383   0.588476    0.6046263   0.6193401
  0.6325719   0.6442794   0.6544244   0.66297233  0.66989255  0.67515844
  0.6787475   0.6806414   0.68082625  0.67929226  0.67603415  0.671051
  0.6643464   0.65592825  0.6458091   0.6340058   0.6205396   0.6054363
  0.588726    0.5704429   0.55062574  0.5293172   0.506564    0.482417
  0.45693067  0.43016338  0.402177    0.3730369   0.34281164  0.31157306
  0.27939582  0.24635741  0.21253791  0.1780198   0.14288774  0.10722836
  0.07113006  0.03468278 -0.0020222  -0.03889256 -0.0758351  -0.11275602
 -0.14956115 -0.1861562  -0.22244696 -0.25833964 -0.29374105 -0.32855877
 -0.3627016  -0.3960796  -0.42860442 -0.46018958 -0.49075055 -0.52020514
 -0.54847366 -0.5754791  -0.60114735 -0.6254075  -0.648192   -0.66943663
 -0.6890811  -0.7070688  -0.7233473  -0.73786825 -0.75058764 -0.76146597
 -0.77046824 -0.77756417 -0.78272825 -0.7859399  

tf.Tensor(
[-0.35787106 -0.38273746 -0.40679795 -0.42998523 -0.4522341  -0.47348148
 -0.49366656 -0.512731   -0.53061897 -0.5472774  -0.562656   -0.5767076
 -0.5893881  -0.60065657 -0.6104756  -0.61881125 -0.62563324 -0.6309149
 -0.6346335  -0.63677    -0.63730955 -0.6362412  -0.6335581  -0.6292575
 -0.62334085 -0.61581373 -0.60668594 -0.5959714  -0.58368826 -0.56985885
 -0.55450946 -0.5376706  -0.5193768  -0.4996664  -0.4785817  -0.45616874
 -0.4324773  -0.40756068 -0.38147563 -0.35428226 -0.32604384 -0.2968267
 -0.2667     -0.23573571 -0.2040083  -0.17159456 -0.13857353 -0.10502619
 -0.07103534 -0.03668533 -0.0020619   0.03274808  0.06765679  0.10257572
  0.13741586  0.17208795  0.20650272  0.2405711   0.27420446  0.30731487
  0.3398153   0.3716198   0.40264386  0.43280458  0.4620208   0.49021348
  0.51730573  0.54322326  0.56789434  0.5912501   0.61322486  0.63375604
  0.6527845   0.6702548   0.6861152   0.70031786  0.7128189   0.7235788
  0.7325622   0.73973817  0.74508035  0.74856

tf.Tensor(
[-1.27306327e-01 -1.02537647e-01 -7.73276538e-02 -5.17368466e-02
 -2.58274041e-02  3.37064732e-04  2.66917516e-02  5.31708375e-02
  7.97076821e-02  1.06234998e-01  1.32685021e-01  1.58989713e-01
  1.85080886e-01  2.10890427e-01  2.36350477e-01  2.61393547e-01
  2.85952777e-01  3.09962064e-01  3.33356261e-01  3.56071323e-01
  3.78044516e-01  3.99214566e-01  4.19521838e-01  4.38908517e-01
  4.57318723e-01  4.74698752e-01  4.90997136e-01  5.06164849e-01
  5.20155430e-01  5.32925189e-01  5.44433177e-01  5.54641545e-01
  5.63515425e-01  5.71023166e-01  5.77136457e-01  5.81830382e-01
  5.85083485e-01  5.86877942e-01  5.87199450e-01  5.86037517e-01
  5.83385348e-01  5.79239964e-01  5.73602259e-01  5.66476822e-01
  5.57872295e-01  5.47801018e-01  5.36279321e-01  5.23327291e-01
  5.08968890e-01  4.93231803e-01  4.76147443e-01  4.57750946e-01
  4.38080996e-01  4.17179823e-01  3.95093113e-01  3.71869832e-01
  3.47562253e-01  3.22225720e-01  2.95918554e-01  2.68701971e-01
  2.40639910e-

 -0.82828385], shape=(121,), dtype=float32)
tf.Tensor(
[ 0.19534104  0.19027863  0.18468565  0.17857109  0.17194545  0.16482067
  0.15721007  0.14912835  0.14059156  0.13161707  0.12222353  0.11243082
  0.10226005  0.09173349  0.08087452  0.06970758  0.05825815  0.04655266
  0.03461843  0.02248365  0.01017726 -0.00227107 -0.01483103 -0.02747176
 -0.04016188 -0.05286959 -0.06556275 -0.07820897 -0.09077564 -0.10323007
 -0.11553954 -0.1276714  -0.13959315 -0.1512725  -0.16267748 -0.17377654
 -0.18453859 -0.19493312 -0.20493026 -0.2145009  -0.22361672 -0.2322503
 -0.2403752  -0.24796605 -0.25499856 -0.26144966 -0.26729757 -0.2725218
 -0.2771033  -0.2810245  -0.28426924 -0.2868231  -0.28867316 -0.28980824
 -0.29021883 -0.28989723 -0.28883755 -0.28703567 -0.28448936 -0.28119826
 -0.2771639  -0.27238974 -0.26688114 -0.26064542 -0.2536918  -0.24603139
 -0.23767725 -0.2286443  -0.21894935 -0.20861104 -0.19764984 -0.18608797
 -0.1739494  -0.16125982 -0.1480465  -0.13433832 -0.12016571 -0.1055605

 -9.36537802e-01], shape=(121,), dtype=float32)
tf.Tensor(
[-0.536903   -0.52124786 -0.50418437 -0.4857458  -0.46596986 -0.44489843
 -0.42257714 -0.39905533 -0.3743858  -0.34862468 -0.32183123 -0.29406783
 -0.26539963 -0.23589459 -0.20562315 -0.17465816 -0.14307469 -0.11094981
 -0.07836241 -0.04539306 -0.01212372  0.02136238  0.05498103  0.08864716
  0.12227516  0.155779    0.18907256  0.22206974  0.25468475  0.28683233
  0.31842798  0.34938815  0.3796305   0.40907413  0.43763968  0.46524972
  0.49182886  0.517304    0.5416044   0.56466216  0.5864121   0.60679203
  0.62574315  0.64320993  0.6591404   0.67348635  0.6862033   0.69725084
  0.70659256  0.7141964   0.7200345   0.7240835   0.72632444  0.72674304
  0.7253296   0.722079    0.71699095  0.7100698   0.70132464  0.69076943
  0.6784227   0.6643077   0.6484524   0.6308893   0.6116555   0.5907925
  0.5683462   0.54436684  0.51890874  0.49203026  0.4637937   0.4342651
  0.40351415  0.3716139   0.33864072  0.30467406  0.2697962   0.234

...

tf.Tensor(
[ 0.33093894  0.33962902  0.347535    0.35462955  0.36088723  0.3662847
  0.37080064  0.37441587  0.3771133   0.37887818  0.3796979   0.3795622
  0.37846324  0.37639552  0.373356    0.36934412  0.36436173  0.35841328
  0.35150567  0.3436483   0.33485317  0.3251347   0.31450984  0.30299798
  0.29062095  0.277403    0.26337072  0.24855302  0.23298109  0.21668826
  0.19971003  0.18208395  0.16384953  0.14504817  0.1257231   0.1059192
  0.085683    0.06506249  0.04410707  0.02286739  0.00139525 -0.02025652
 -0.04203421 -0.06388333 -0.08574876 -0.1075749  -0.1293058  -0.15088525
 -0.17225705 -0.19336502 -0.21415322 -0.23456606 -0.25454852 -0.27404615
 -0.2930054  -0.31137362 -0.32909924 -0.34613198 -0.36242288 -0.37792456
 -0.39259124 -0.40637892 -0.41924557 -0.43115112 -0.4420577  -0.45192966
 -0.46073377 -0.4684393  -0.47501805 -0.48044452 -0.48469597 -0.4877525
 -0.48959714 -0.4902159  -0.4895978  -0.48773497 -0.48462272 -0.48025948
 -0.47464693 -0.46778992 -0.4596966  -0.4503

tf.Tensor(
[-0.3306538  -0.32783037 -0.32415178 -0.31961933 -0.3142367  -0.3080099
 -0.30094722 -0.29305917 -0.28435853 -0.27486023 -0.2645814  -0.25354138
 -0.24176155 -0.2292654  -0.21607849 -0.20222832 -0.18774436 -0.17265795
 -0.15700226 -0.14081219 -0.12412433 -0.10697684 -0.08940941 -0.07146314
 -0.05318045 -0.03460501 -0.0157816   0.00324398  0.02242501  0.04171395
  0.06106261  0.08042222  0.09974353  0.11897702  0.13807294  0.15698145
  0.17565282  0.19403744  0.21208604  0.2297498   0.24698047  0.2637305
  0.27995312  0.29560262  0.31063426  0.32500458  0.33867142  0.3515941
  0.36373344  0.37505203  0.3855142   0.39508614  0.4037361   0.41143447
  0.4181537   0.42386863  0.42855644  0.43219674  0.4347717   0.436266
  0.43666705  0.4359649   0.43415242  0.43122518  0.42718163  0.42202303
  0.41575357  0.4083803   0.39991313  0.3903649   0.37975127  0.3680908
  0.3554049   0.3417178   0.3270564   0.31145042  0.29493216  0.27753657
  0.25930113  0.24026571  0.22047262  0.199966

tf.Tensor(
[ 8.39418825e-03  8.18164367e-03  7.94620533e-03  7.68824061e-03
  7.40817748e-03  7.10650487e-03  6.78377040e-03  6.44058129e-03
  6.07760297e-03  5.69555722e-03  5.29522169e-03  4.87742852e-03
  4.44306247e-03  3.99305858e-03  3.52840172e-03  3.05012334e-03
  2.55930028e-03  2.05705152e-03  1.54453667e-03  1.02295284e-03
  4.93532280e-04 -4.24605896e-05 -5.83731919e-04 -1.12896145e-03
 -1.67680567e-03 -2.22590100e-03 -2.77486653e-03 -3.32230842e-03
 -3.86682246e-03 -4.40699747e-03 -4.94141970e-03 -5.46867540e-03
 -5.98735455e-03 -6.49605505e-03 -6.99338596e-03 -7.47797173e-03
 -7.94845447e-03 -8.40349868e-03 -8.84179492e-03 -9.26206261e-03
 -9.66305379e-03 -1.00435587e-02 -1.04024047e-02 -1.07384650e-02
 -1.10506574e-02 -1.13379499e-02 -1.15993628e-02 -1.18339742e-02
 -1.20409187e-02 -1.22193927e-02 -1.23686586e-02 -1.24880429e-02
 -1.25769433e-02 -1.26348278e-02 -1.26612373e-02 -1.26557890e-02
 -1.26181766e-02 -1.25481728e-02 -1.24456286e-02 -1.23104779e-02
 -1.21427365e-

tf.Tensor(
[ 0.1985281   0.19028255  0.18147787  0.17213105  0.16226065  0.15188685
  0.1410313   0.12971708  0.11796871  0.105812    0.09327407  0.08038328
  0.06716912  0.05366221  0.03989419  0.02589765  0.01170609 -0.00264621
 -0.01712422 -0.03169229 -0.04631418 -0.06095319 -0.07557226 -0.090134
 -0.10460086 -0.11893516 -0.13309923 -0.14705546 -0.16076645 -0.1741951
 -0.18730463 -0.2000588  -0.21242192 -0.22435898 -0.23583572 -0.24681875
 -0.25727567 -0.26717508 -0.27648672 -0.28518158 -0.29323196 -0.3006116
 -0.30729556 -0.31326064 -0.31848517 -0.32294917 -0.32663444 -0.3295246
 -0.3316052  -0.33286366 -0.3332894  -0.33287394 -0.3316108  -0.3294956
 -0.3265262  -0.32270247 -0.3180266  -0.31250292 -0.30613795 -0.29894045
 -0.2909214  -0.28209388 -0.2724733  -0.26207712 -0.250925   -0.23903869
 -0.22644198 -0.21316072 -0.19922274 -0.18465777 -0.16949742 -0.1537751
 -0.13752595 -0.12078676 -0.1035959  -0.08599323 -0.06802001 -0.0497188
 -0.03113339 -0.01230866  0.00670952  0.02587437

KeyboardInterrupt: 

In [23]:
data_train


<TakeDataset shapes: (3, 121), types: tf.float32>